# 0. PARAMETERS

### 0.1 Packages

In [4]:
#Partie 1
import requests
import json
import os 
import subprocess
import pandas as pd
import overpy
import dicttoxml
import overpass

#Partie 2
import sumolib
import sys 
import numpy as np


##Partie 3
import xml.etree.ElementTree as ET

#Partie 4
import webbrowser
import os
import time 
from datetime import datetime

### 0.2 Parameters definiton

In [5]:
# 1. OSM data
# 1.1 Query OSM data
counties_name = ["Los Angeles", "Contra Costa"]
path = '/Users/edouardlabarthe/Documents/Edouard/US/Research/CODE/'
output_name = "LA_CS"

network_path = "/Users/edouardlabarthe/Documents/Edouard/US/Research/CODE"
network_file = "LA_CS_network.net.xml"

# 2. FLOW DATA 
network_path = "/Users/edouardlabarthe/Documents/Edouard/US/Research/CODE"



# 3. DETECTOR DATA
# 2.1 Detector
districts_id = ["7", "4"]
counties_id = ["37", "111", "13" ]
interstates_id = ['5', '80', '10', '580', '105', '680', '110', '210' ,'405', '605', '710']
detectors_raw_file = "vds_config.xml" # Accessible in PeMS help section



# Need to automate download
pems_path = "/Users/edouardlabarthe/Documents/Edouard/US/Research/PeMS"
lat_log_file = "lat_log.xlsx"
file_inductor = "test_data.xlsx"

# File name
detector_file_name = "LA_CS_detector.xml"

# 1. OSM DATA

### 1.1 Query OSM data


https://sumo.dlr.de/docs/Networks/Import/OpenStreetMap.html

Modify the query here: 

In [66]:
# Query OSM data using open street map
def fetch_osm_data(counties, path, output_name):
    overpass_url = "http://overpass-api.de/api/interpreter"

    #Used
    query_bodies = ''
    for idx, county in enumerate(counties):

        overpass_query_body = '''area["county:name"="''' + county + '''"]->.searchArea''' + str(idx) + ''';
                                (
                                    (
                                    node["highway"="motorway"][~"^ref$"~"^I"](area.searchArea''' + str(idx) + ''');  
                                    way["highway"="motorway"][~"^ref$"~"^I"](area.searchArea''' + str(idx) + ''');
                                    )->.a''' + str(idx) + ''';	
                                    (
                                    node(w.a''' + str(idx) + ''')["highway"="motorway_juction"](area.searchArea''' + str(idx) + ''');
                                    way(around.a''' + str(idx) + ''':5)["highway"="motorway_link"](area.searchArea''' + str(idx) + ''');	
                                    );
                                );'''
    
        query_bodies = query_bodies + overpass_query_body

    total_query = '''
                    [out:xml][timeout:1000];
                    ( 
                    ''' + query_bodies + ''' 
                    );
                    out meta;
                    >;
                    out meta; 
                    '''
        
    response = requests.get(overpass_url, params={'data': total_query}, )

    #Write the file
    f = open(path + output_name + '.osm', "w")
    f.write(response.text)
    f.close() 

In [67]:
fetch_osm_data(counties_name, path, output_name)

### 1.2 Go through JOSM for file cleaning 

Manually upload the downloaded OSM data into JOSM software and dowloard the resulting file from JOSM. 

### 1.3. Apply Netconvert

In [ ]:
%cd /Users/edouardlabarthe/Documents/Edouard/US/Research/CODE

!netconvert --osm-files LA_CS_JOSM.osm --o LA_CS_network.net.xml --geometry.remove --ramps.guess --junctions.join --tls.guess-signals --tls.discard-simple --tls.join --tls.default-type actuated

%cd /Users/edouardlabarthe/Documents/Edouard/US/Research/CODE

# 2. FLOW DATA

### 2.1 Retreiving flow informations

In [6]:
flow_path  = "/Users/edouardlabarthe/Documents/Edouard/US/Research/PeMS/flow_files"

def retreive_flow_data(flow_path, interstates_id):

    list_dir = os.listdir(flow_path)

    flow = pd.DataFrame()
    for file in list_dir:

        flow_temp = pd.read_csv(flow_path + "/" + file, sep=",", header=None)
        flow = pd.concat([flow, flow_temp])

    # Build collumns names
    flow_col = ['Timestamp', 'Station', 'District', 'Freeway', 'Direction of Travel', 'Lane Type', 'Station Length', 'Samples', '% Observed', 'Total Flow', 'Avg Occupancy', 'Avg Speed']
    nb_max_lanes = int((flow.shape[1] - 12 )/5)

    for lane in range(nb_max_lanes):
        new_cols = [ 'Lane ' + str(lane) + ' Samples','Lane ' + str(lane) + ' Flow', 'Lane ' + str(lane) + ' Avg Occ', 'Lane ' + str(lane) + ' Avg Speed', 'Lane ' + str(lane) + ' Observed']
        
        for col in new_cols:
            flow_col.append(col)

    # Clean the filter flow table
    flow.columns = flow_col
    flow = flow[flow['Freeway'].isin(interstates_id)]

    return flow

In [7]:
flow = retreive_flow_data(flow_path, interstates_id)

### 2.2 Understanding the data

In [8]:
# Missing values per variable per type of VDS
flow_col = flow.columns
type_vds = flow["Lane Type"].unique()

inte = flow[flow["Lane Type"].isin(['ML', "OR"])]

for col in flow_col:
    ratio = inte[inte[col].isnull()].shape[0] / flow.shape[0]
    print(col, ratio)

Timestamp 0.0
Station 0.0
District 0.0
Freeway 0.0
Direction of Travel 0.0
Lane Type 0.0
Station Length 0.21583012489435627
Samples 0.0
% Observed 0.0
Total Flow 0.10987864177387548
Avg Occupancy 0.10987864177387548
Avg Speed 0.21583012489435627
Lane 0 Samples 0.0
Lane 0 Flow 0.11082980209409334
Lane 0 Avg Occ 0.11082980209409334
Lane 0 Avg Speed 0.21583012489435627
Lane 0 Observed 0.0
Lane 1 Samples 0.2104422950511785
Lane 1 Flow 0.21456240022537326
Lane 1 Avg Occ 0.21456240022537326
Lane 1 Avg Speed 0.21678091839609354
Lane 1 Observed 0.0
Lane 2 Samples 0.2202671612357968
Lane 2 Flow 0.22058409240304253
Lane 2 Avg Occ 0.22058409240304253
Lane 2 Avg Speed 0.22058409240304253
Lane 2 Observed 0.0
Lane 3 Samples 0.2808010141797352
Lane 3 Flow 0.2808010141797352
Lane 3 Avg Occ 0.2808010141797352
Lane 3 Avg Speed 0.2808010141797352
Lane 3 Observed 0.0
Lane 4 Samples 0.5093083857639215
Lane 4 Flow 0.5093083857639215
Lane 4 Avg Occ 0.5093083857639215
Lane 4 Avg Speed 0.5093083857639215
Lane 

In [9]:
type_vds = flow["Lane Type"].unique()

for type in type_vds:
   ratio = flow[flow["Lane Type"] == type].shape[0] / flow.shape[0]
   print(type, ratio)

ML 0.37786411869659126
OR 0.21583012489435627
FR 0.1610010329608414
HV 0.19142642501643348
FF 0.04437036341440511
CD 0.009507935017372524


In [10]:
flow

Timestamp  Station  District  Freeway Direction of Travel  \
0        01/02/2022 00:00:00   715898         7        5                   S   
1        01/02/2022 00:00:00   715900         7        5                   S   
2        01/02/2022 00:00:00   715901         7        5                   N   
3        01/02/2022 00:00:00   715903         7        5                   N   
4        01/02/2022 00:00:00   715904         7        5                   S   
...                      ...      ...       ...      ...                 ...   
1410981  01/01/2022 23:55:00   777254         7      710                   S   
1410982  01/01/2022 23:55:00   777262         7      710                   N   
1410983  01/01/2022 23:55:00   777263         7      710                   S   
1410984  01/01/2022 23:55:00   777285         7      405                   S   
1410985  01/01/2022 23:55:00   777292         7       10                   W   

        Lane Type  Station Length  Samples  % Observed  Total Flow  ...  \
0              ML           0.430        0           0       353.0  ...   
1              OR             NaN        0           0         NaN  ...   
2              OR             NaN        0           0         NaN  ...   
3              OR             NaN        0           0         NaN  ...   
4              OR             NaN        0           0         NaN  ...   
...           ...             ...      ...         ...         ...  ...   
1410981        ML           0.150       30           0       320.0  ...   
1410982        ML           0.490       30           0       320.0  ...   
1410983        ML           0.490       30           0       320.0  ...   
1410984        FR             NaN       10           0         NaN  ...   
1410985        HV           2.639        0           0       106.0  ...   

         Lane 6 Samples  Lane 6 Flow  Lane 6 Avg Occ  Lane 6 Avg Speed  \
0                   NaN          NaN             NaN               NaN   
1                   NaN          NaN             NaN               NaN   
2                   NaN          NaN             NaN               NaN   
3                   NaN          NaN             NaN               NaN   
4                   NaN          NaN             NaN               NaN   
...                 ...          ...             ...               ...   
1410981             NaN          NaN             NaN               NaN   
1410982             NaN          NaN             NaN               NaN   
1410983             NaN          NaN             NaN               NaN   
1410984             NaN          NaN             NaN               NaN   
1410985             NaN          NaN             NaN               NaN   

         Lane 6 Observed  Lane 7 Samples  Lane 7 Flow  Lane 7 Avg Occ  \
0                      0             NaN          NaN             NaN   
1                      0             NaN          NaN             NaN   
2                      0             NaN          NaN             NaN   
3                      0             NaN          NaN             NaN   
4                      0             NaN          NaN             NaN   
...                  ...             ...          ...             ...   
1410981                0             NaN          NaN             NaN   
1410982                0             NaN          NaN             NaN   
1410983                0             NaN          NaN             NaN   
1410984                0             NaN          NaN             NaN   
1410985                0             NaN          NaN             NaN   

         Lane 7 Avg Speed  Lane 7 Observed  
0                     NaN                0  
1                     NaN                0  
2                     NaN                0  
3                     NaN                0  
4                     NaN                0  
...                   ...              ...  
1410981               NaN                0  
1410982               NaN      

In [11]:
flow.shape

(2726144, 52)

In [14]:
def flow_by_col(flow):
    # We decided to only take to ML type of detectors
    flow = flow[flow["Lane Type"].isin(['ML'])]

    flow_lanes = flow.iloc[: , 12:]
    flow_lanes = flow_lanes.iloc[:,[1, 3, 6, 8, 11, 13, 16, 18, 21, 23, 26, 28, 31, 33, 36, 38]]

    lanes = flow_lanes.isnull().sum(axis=1).tolist()
    lanes = [int((16-x)/ 2) for x in lanes]

    flow['nb_lanes'] = lanes
    
    # What is the max number of lanes
    nb_max_lanes = int((flow.shape[1] - 12 )/5)

    # Duplicate each line by the number of max lanes
    #flow_dupli = pd.DataFrame(np.repeat(flow.values, nb_max_lanes, axis=0))
    #flow_dupli.columns = flow.columns

    flow_dupli = flow.loc[flow.index.repeat(flow.nb_lanes)]

    #Change the name of the station + keep only interesting stuff
    for row in range(flow_dupli.shape[0]):
        for i in lanes:
            flow_dupli['Station'][i] =  flow_dupli['Station'][i] + "_" + str(i)

            #List of columns:

            flow_dupli["flow"] = flow_dupli.iloc[ 14 + i*5 ]
            flow_dupli["speed"] = flow_dupli.iloc[ 16 + i*5 ]
        row = row + 1

   # flow_dupli = flow_dupli['Timestamp', 'Station', 'District', 'Freeway', 'Direction of Travel', 'Lane Type', 'Station Length', 'Samples', '% Observed', 'Total Flow', 'Avg Occupancy', 'Avg Speed', 'flow', 'speed']

    return flow_dupli


In [15]:
flow_dupli = flow_by_col(flow)

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # This is added back by InteractiveShellApp.init_path()


KeyError: 3

In [19]:
flow_lanes = flow.iloc[: , 12:]
flow_lanes = flow_lanes.iloc[:,[1, 3, 6, 8, 11, 13, 16, 18, 21, 23, 26, 28, 31, 33, 36, 38]]

lanes = flow_lanes.isnull().sum(axis=1).tolist()
lanes = [int((16-x)/ 2) for x in lanes]

for row in range(flow_lanes.shape[0]):
    for i in lanes:
        print(row)
    row = row + i 

0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


In [16]:
flow_dupli

NameError: name 'flow_dupli' is not defined

In [217]:
flow_processed = flow[flow["Lane Type"] == "ML"]
flow_processed = flow[["Station", 'Timestamp', "Total Flow", "Avg Speed"]]
flow_processed.columns = ["Detector_id", "Time", "Number_of_passenger_cars", "Average_speed_of_passenger_cars"]

In [ ]:
detector_id_cut = [str(x)[:6] for x in detectors_id]

split

In [ ]:
df = pd.DataFrame((zip(detectors_id, detector_id_cut)), columns=["det_id", "Detector_id"])
df["count"] = df.Detector_id.apply(lambda row: detector_id_cut.count(str(row)))

time_recorded = df_total['Time'].unique()

df_temp = df
df_final = pd.DataFrame()
for idx, t in enumerate(time_recorded):
    df_temp["Time"] = t
    
    df_final = pd.concat([df_final, df_temp])

df_final["Time"].unique()

df_final = df_final.astype({'Detector_id': 'int64'})
df_final_2 = df_final.merge(df_total, how="left", on=["Detector_id", 'Time'])

df_final_2["Number_of_passenger_cars"] = df_final_2.Number_of_passenger_cars.apply(lambda row: df_final_2.Number_of_passenger_cars[row]/df_final_2['count'][row])




In [ ]:
df_final_2 = df_final_2[["det_id", 'Time', "Number_of_passenger_cars", "Average_speed_of passenger_cars"]]
df_final_2.columns = ["Detector", "Time", "qPKW", "vPKW"]

# Convert time to sum of minutes 
df_final_2["Time"] = [pd.to_datetime(date, format ="%H:%M").time() for date in df_final_2["Time"].to_list()]
df_final_2["Time"] = df_final_2["Time"].apply(lambda x: x.hour*60 + x.minute)

# Convert to floats 
df_final_2 = df_final_2.astype(int)

#Save the file
df_final_2.to_csv("flow.csv", sep=';', index=False)

# 3. DETECTOR DATA

What we do ? 

### 3.1. Retreiving detector informations

In [154]:
def retreive_detectors_data(file_name, districts_id, counties_id, interstates_id):

    # Read the file using ElementTree package
    tree = ET.parse('vds_config.xml')

    # getting the parent tag of
    # the xml document
    root = tree.getroot()

    #Initiate the rows
    rows = []

    # Can probably automate cols retreival. 
    df_cols = ['id', "name", 'type', 'county_id', 'city_id', 'freeway_id', 'freeway_dir', 'lanes', 'cal_pm', 'abs_pm', 'latitude', 'longitude', 'last_modified']

    # Iterate on the districts and only take those who are intersting
    for disctrict in root: 
        if disctrict.attrib.get("id") in districts_id:

            for vds in disctrict[1]:

                res = []
                res.append(vds.attrib.get(df_cols[0]))
                for el in df_cols[1:]:
                    res.append(vds.attrib.get(el) )

                rows.append({df_cols[i]: res[i] 
                            for i, _ in enumerate(df_cols)})
                
    out_df = pd.DataFrame(rows, columns=df_cols)

    out_df = out_df[out_df['county_id'].isin(counties_id)]
    out_df = out_df[out_df['freeway_id'].isin(interstates_id)]

    df_inductor = out_df[["id", "latitude", "longitude"]]
    df_inductor.columns = ["VDS", "lat", "lon"]
    df_inductor["VDS"] = pd.to_numeric(df_inductor["VDS"])
    df_inductor["lat"] = pd.to_numeric(df_inductor["lat"], downcast="float")
    df_inductor["lon"] = pd.to_numeric(df_inductor["lon"], downcast="float")

    df_inductor_array = df_inductor.to_numpy()

    return(out_df, df_inductor_array)

In [ ]:
df_inductor, df_inductor_array = retreive_detectors_data(detectors_raw_file, districts_id, counties_id, interstates_id)

Creation of the detector file

In [193]:
def create_detectors(network_file,df_inductor_array):
   
    sys.path.append(os.path.join(os.environ["SUMO_HOME"], 'tools'))

    # Import network and define list
    net = sumolib.net.readNet(network_file)
    detectors = []
    detectors_array = []

    i = 0
    #Loop for every detector
    for id, lon, lat in df_inductor_array:
        xy_pos = net.convertLonLat2XY(lat, lon)
        
        # look 10m around the position
        lanes = net.getNeighboringLanes(xy_pos[0], xy_pos[1], 1000)
        i = i+1
        
        # attention, result is unsorted
        bestLane = None
        ref_d = 9999.

        for lane, dist in lanes:
            # now process them and determine a "bestLane"
            # ...
            if dist < ref_d:
                ref_d = dist
                bestLane = lane

            pos, d = bestLane.getClosestLanePosAndDist(xy_pos)
            freq=300.00
            file = "detector_simulated.xml"
        
        if bestLane != None:
            id_bestLane = bestLane.getID()
        else:
            id_bestLane = "00_0"

        #Save information to use in the lane duplication process
        detector = [int(id), id_bestLane, pos, freq, file]
        detectors_array.append(detector)
        
    return detectors_array

Duplicate detectors for every lane

In [194]:
def additional_detectors(detectors_array,df_inductor):

    #Add the lane information with df_lane
    detector_df = pd.DataFrame(detectors_array, columns = ["VDS",'lane','position', "freq", "file"])

    df_lane = df_inductor[["id", 'lanes']]
    df_lane.columns = ["VDS", '# Lane Points']
    df_lane["VDS"] = pd.to_numeric(df_lane["VDS"])

    
    detector_df_lane = detector_df.merge(df_lane, how="inner", on= 'VDS').drop_duplicates()

    # Count the nb of time the is an error
    error = 0

    # Loop through the old detectors
    for i in range(detector_df_lane.shape[0]):
        
        #Number of lane at this moment in the road
        total_lane = int(detector_df_lane['# Lane Points'].iloc[i])  
        
        #Current lane positon on the detector
        lane_nb = int(detector_df_lane['lane'].iloc[i][-1])
        
        #List of all other lanes
        list_lane = [*range(total_lane)]
        if lane_nb != total_lane and lane_nb < total_lane:
            list_lane.remove(lane_nb)
            error = error+1

        #For empty lane, add a detector
        for y in list_lane:
            id = str(detector_df_lane['VDS'].iloc[i]) + str(y)
            lane = detector_df_lane['lane'].iloc[i][:-1] + str(y)
            positon = detector_df_lane['position'].iloc[i]
            freq = 300.00
            file = "detector_simulated.xml"
            
            detector = [int(id), lane, positon, freq, file]
            detectors_array.append(detector)

    return detectors_array, error
        

Save it in a detector.xml file

In [195]:
def write_additional_file (network_file, df_inductor, df_inductor_array, detector_file_name):

    old_detectors = create_detectors(network_file, df_inductor_array)
    #print(old_detectors)
    total_detectors, error = additional_detectors(old_detectors, df_inductor)

    detectors = []
    detectors_id = []

    for i in total_detectors:

        #Save information in detctor.xml
        detectors_id.append(i[0])
        detectors.append(sumolib.sensors.inductive_loop.InductiveLoop((i[0]), i[1], i[2], i[3], i[4]))
        sumolib.files.additional.write(detector_file_name, detectors)

    return detectors_id

In [223]:
detectors_id = write_additional_file(network_file, df_inductor, df_inductor_array, detector_file_name)

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


File finished: LA_CS_detector_processed.xml

## 2.2 FLOW FILE

FILE FORMAT:

Detector_id; Time(minutes); Number_of_passenger_cars; Number_of_trucks; Average_speed_of passenger_cars; Average_speed_of_trucks

TIME OF SOURCE FILE: 
- 2D trop compliqué
- Contour 1: celle à utiliser

URL EXAMPLE:

https://pems.dot.ca.gov/?report_form=1&dnode=Freeway&content=spatial&tab=spatial2d&export=xls&fwy=10&dir=E&s_time_id=1652659200&s_time_id_f=05%2F16%2F2022+00%3A30&start_pm=.17&end_pm=239.92&crossings=&station_type=ml&agg=on&lane1=on&lane2=on&lane3=on&lane4=on&lane5=on&lane6=on&q=occ

#### 2.2.A Download the PeMS files

In [218]:
def download_PeMS(start_datetime, end_datetime, quantity):
    """
    Quantity = occ, speed, flow
    Date should be entered as follow: %d/%m/%y
    """
    
    # Put date in datetime format
    start = datetime.strptime(start_datetime, "%d/%m/%y")
    end = datetime.strptime(end_datetime, "%d/%m/%y")

    # Create list of date spaced by the increment
    l = (pd.DataFrame(columns=['NULL'],
                  index=pd.date_range(start, end,
                                      freq='1D'))
       .index.strftime('%d/%m/%y')
       .tolist()
       )

    # Define the second count
    reference_time = datetime.strptime("2022-05-16T00:00:00Z", "%Y-%m-%dT%H:%M:%SZ" )
    print(l)

    #iterate every 5 min
    for i, date in enumerate(l):
        #Date
        date_2 = datetime.strptime(date, "%d/%m/%y" )
        year = date_2.year
        month = date_2.month
        day = date_2.day
        hour = date_2.hour
        minute = date_2.minute

        #Second
        difference = (reference_time - date_2)
        total_seconds = round(1652659200 - difference.total_seconds())
        
        #URL
        quantity
        #url_2D = "https://pems.dot.ca.gov/?report_form=1&dnode=Freeway&content=spatial&tab=spatial2d&export=xls&fwy=10&dir=E&s_time_id=" + str(total_seconds) +  "&s_time_id_f=" + str(month) + "%2F0" + str(day) + "%2F" + str(year) + "+" + str(hour) + "%3A" + str(minute) + "&start_pm=.17&end_pm=239.92&crossings=&station_type=ml&agg=on&lane1=on&lane2=on&lane3=on&lane4=on&lane5=on&lane6=on&q=" + "occ"
        url_TS = "https://pems.dot.ca.gov/?report_form=1&dnode=Freeway&content=spatial&tab=contours&export=xls&fwy=10&dir=E&county_id=37&s_time_id=" + str(total_seconds) +"&s_time_id_f=" + str(month) + "%2F" + str(day) + "%2F" + str(year) + "&from_hh=0&to_hh=23&start_pm=.17&end_pm=46.72&lanes=&station_type=ml&q=" + str(quantity) + "&colormap=30%2C31%2C32&sc=auto&ymin=&ymax=&view_d=2"

        webbrowser.open(url_TS)

    return i 

In [219]:
nb_files = download_PeMS("12/12/21","13/12/21","flow")
nb_files = download_PeMS("12/12/21","13/12/21","speed")

['12/12/21', '13/12/21']
['12/12/21', '13/12/21']


#### 2.2.B Fetch and merge the downloaded files 

In [220]:
def merge_PeMS(nb_days, file_nb):

    """
    Nb_days: tells how many files need to be fetch
    File_nb: tells how many output file already exist on the computer
    """

    #Fetch downloaded files
    path = "/Users/edouardlabarthe/Downloads"
    for x in range(nb_days):
        #flow
        if x == 0 and file_nb==0:
            file = path + '/pems_output.xlsx'
            df_flow = pd.read_excel(file)

        if x == 0 and file_nb!=0:
            file = path + '/pems_output (' + str(x+file_nb) + ').xlsx'
            df_flow = pd.read_excel(file)

        else: 
            file = path + '/pems_output (' + str(x+file_nb) + ').xlsx'
            df = pd.read_excel(file)

            df_flow = pd.concat([df_flow,df])

        #Speed
        if x == 0:
            file = path + '/pems_output (' + str(nb_days+x+file_nb) + ').xlsx'
            df_speed = pd.read_excel(file)
        
        else:
            file = path + '/pems_output (' + str(nb_days+x+file_nb) + ').xlsx'
            df = pd.read_excel(file)
            
            df_speed = pd.concat([df_speed,df])

    #Other task
    else:
        df_total = df_speed
        df_total["AggFlow"] = df_flow["AggFlow"]

        #For now trucks are not taken into acount
        df_total["Number_of_trucks"] = 0
        df_total["Average_speed_of_trucks"] = 0

    return df_total


In [222]:
df_total = merge_PeMS(nb_files, 1)

KeyError: 'AggFlow'

#### 2.2.C Clean the file

In [ ]:
df_lane = df_total[['VDS', '# Lane Points']]
df_lane = df_lane.drop_duplicates()

df_total = df_total[["VDS", 'Time', "AggFlow", "Number_of_trucks", "AggSpeed", "Average_speed_of_trucks"]]
df_total.columns = ["Detector_id", "Time", "Number_of_passenger_cars", "Number_of_trucks", "Average_speed_of passenger_cars", "Average_speed_of_trucks"]

In [ ]:
df_total = df_total[["VDS", 'Time', "AggFlow", "Number_of_trucks", "AggSpeed", "Average_speed_of_trucks"]]
df_total.columns = ["Detector_id", "Time", "Number_of_passenger_cars", "Number_of_trucks", "Average_speed_of passenger_cars", "Average_speed_of_trucks"]

#### 2.2.D. SPLIT BY LANE

In [ ]:
detector_id_cut = [str(x)[:6] for x in detectors_id]


In [ ]:
df = pd.DataFrame((zip(detectors_id, detector_id_cut)), columns=["det_id", "Detector_id"])
df["count"] = df.Detector_id.apply(lambda row: detector_id_cut.count(str(row)))

time_recorded = df_total['Time'].unique()

df_temp = df
df_final = pd.DataFrame()
for idx, t in enumerate(time_recorded):
    df_temp["Time"] = t
    
    df_final = pd.concat([df_final, df_temp])

df_final["Time"].unique()

df_final = df_final.astype({'Detector_id': 'int64'})
df_final_2 = df_final.merge(df_total, how="left", on=["Detector_id", 'Time'])

df_final_2["Number_of_passenger_cars"] = df_final_2.Number_of_passenger_cars.apply(lambda row: df_final_2.Number_of_passenger_cars[row]/df_final_2['count'][row])




det_id Detector_id  count
276  7160281      716028      3
277  7160282      716028      3
49    716028      716028      3
174  7160364      716036      5
173  7160363      716036      5
172  7160362      716036      5
17    716036      716036      5
171  7160360      716036      5
203  7160473      716047      4
26    716047      716047      4
202  7160472      716047      4
201  7160471      716047      4
204  7160500      716050      4
205  7160501      716050      4
206  7160502      716050      4
27    716050      716050      4
218  7160570      716057      4
220  7160573      716057      4
31    716057      716057      4
219  7160572      716057      4

#### 2.2.E. Finish

In [ ]:
df_final_2 = df_final_2[["det_id", 'Time', "Number_of_passenger_cars", "Average_speed_of passenger_cars"]]
df_final_2.columns = ["Detector", "Time", "qPKW", "vPKW"]

# Convert time to sum of minutes 
df_final_2["Time"] = [pd.to_datetime(date, format ="%H:%M").time() for date in df_final_2["Time"].to_list()]
df_final_2["Time"] = df_final_2["Time"].apply(lambda x: x.hour*60 + x.minute)

# Convert to floats 
df_final_2 = df_final_2.astype(int)

#Save the file
df_final_2.to_csv("flow.csv", sep=';', index=False)

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


# 3. RUN PREPROCESSING

In [ ]:
def run_preprocessing():
    for idx, county in enumerate(counties):
        for interstate in interstates: 

            

In [ ]:
counties = ["Los Angeles", "Contra Costa"]


# 4. RUN SIMULATION

### 3.1 Create route file

#### 3.1.A. DFROUTER

In [ ]:
#dfrouter -n interstate_10.net.xml -d detector2.xml -o routes_dfrouter.rou.xml --emitters-output vehicles_dfrouter.rou.xml --measure-files flow.csv

#### 3.1.B. FLOWROUTER.PY

--revalidate-detectors: disregards the source and sink information

In [ ]:
# New cd is used
%cd /Users/edouardlabarthe/sumo/tools/detector

!python3 flowrouter.py -n interstate_10.net.xml -d detector_processed.xml -f flow.csv -o routes_flowrouter.xml -e flows.xml -i 300 --revalidate-detectors -v --debug

flow = open("flows.xml", "rt")
rout = open("routes_flowrouter.xml", "rt")
route = open("routes_flowrouter3.xml", "w")

lines_flow = flow.readlines()
lines_rout = rout.readlines()

end_rout = lines_rout[:1]
lines_flow = lines_flow[1:-1]
lines_rout = lines_rout[:-1]

lines_rout.extend(lines_flow)
lines_rout.extend(end_rout)

route.writelines(lines_rout)

flow.close()
rout.close()
route.close()

# Back to the old repo 
%cd /Users/edouardlabarthe/documents/edouard/US/research/CODE

/Users/edouardlabarthe/sumo/tools/detector
Reading net
837 edges read
Reading detectors
Warning! Edge '119128990' is simultaneously source and sink.
Warning! Edge '148356701' is simultaneously source and sink.
Warning! Edge '148356718' is simultaneously source and sink.
Warning! Edge '148356751' is simultaneously source and sink.
Warning! Edge '148385566' is simultaneously source and sink.
Warning! Edge '148385759' is simultaneously source and sink.
Warning! Edge '149108936' is simultaneously source and sink.
Warning! Edge '156942951' is simultaneously source and sink.
Warning! Edge '156942974' is simultaneously source and sink.
Warning! Edge '156942990' is simultaneously source and sink.
Warning! Edge '156943002' is simultaneously source and sink.
Warning! Edge '156943005' is simultaneously source and sink.
Warning! Edge '24672900' is simultaneously source and sink.
Warning! Edge '24672901' is simultaneously source and sink.
Warning! Edge '24801718' is simultaneously source and sink.


#### 3.1.C. MERGE FLOW AND ROUTE

### 3.2 WRITE THE CONFIG FILE

CONFIG FILE:

https://sumo.dlr.de/xsd/sumoConfiguration.xsd

SSM

- Standard devide equipement procedures
https://sumo.dlr.de/docs/Definition_of_Vehicles%2C_Vehicle_Types%2C_and_Routes.html#devices

    </ssm_device>
    <device.ssm.probability type="floatOptionType"/>
    <device.ssm.explicit" type="strArrayOptionType" minOccurs="0"/>
    <device.ssm.deterministic" type="boolOptionType" minOccurs="0"/>

- SSM Parameters
https://sumo.dlr.de/docs/Simulation/Output/SSM_Device.html

    <device.ssm.measures" type="strOptionType" minOccurs="0"/>
    <device.ssm.thresholds" type="strOptionType" minOccurs="0"/>
    <device.ssm.trajectories" type="boolOptionType" minOccurs="0"/>
    <device.ssm.range" type="floatOptionType" minOccurs="0"/>
    <device.ssm.extratime" type="floatOptionType" minOccurs="0"/>
    <device.ssm.file" type="strOptionType" minOccurs="0"/>
    <device.ssm.geo" type="boolOptionType" minOccurs="0"/>
    <device.ssm.write-positions" type="boolOptionType" minOccurs="0"/>
    <device.ssm.write-lane-positions" type="boolOptionType" minOccurs="0"/>
    </ssm_device>

- SSM output

    <device.ssm.filter-edges.input-file" type="fileOptionType" minOccurs="0"/>

LANE CHANGE 

    <lanechange-output" type="fileOptionType" minOccurs="0"/>
    <lanechange-output.started" type="boolOptionType" minOccurs="0"/>
    <lanechange-output.ended" type="boolOptionType" minOccurs="0"/>
    <lanechange-output.xy" type="boolOptionType" minOccurs="0"/>

COLLISIONS:

- Output

    <collision-output type="fileOptionType" minOccurs="0"/>

- Processing

    <collision.action" type="strOptionType" minOccurs="0"/>
    <collision.stoptime" type="timeOptionType" minOccurs="0"/>
    <collision.check-junctions" type="boolOptionType" minOccurs="0"/>
    <collision.check-junctions.mingap" type="floatOptionType" minOccurs="0"/>
    <collision.mingap-factor" type="floatOptionType" minOccurs="0"/>




In [ ]:
def write_config_file(start, duration, element): 

    confi_file_name = "flowrouter.sumocfg"

    #Input
    netwo_file_name = "interstate_10.net.xml"
    route_file_name = "routes_flowrouter3.xml"
    detec_file_name = "detector_processed.xml"

    #Output
    collision_output = "collision.xml"
    lane_change_output = "lane_change.xml"

    #Time 
    start_sec= str(start)
    time_sec = str(duration + int(start_sec)) 

    #Processing 
    coll_action = "warn"
    coll_stoptime = str(0)
    coll_check_junctions = "True"
    coll_check_junctions_mingap = str(element)
    coll_mingap_factor = str(element) #is 2.5 by default

    #SSM device
    ssm_file = "ssm.xml"


    config = '''<?xml version="1.0" encoding="iso-8859-1"?>
    <configuration xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance"
    xsi:noNamespaceSchemaLocation="http://sumo.dlr.de/xsd/sumoConfiguration.xsd">
        <input>
            <net-file value="''' + netwo_file_name + '''"/>
            <route-files value="''' + route_file_name + '''"/>
            <additional-files value="''' + detec_file_name + '''"/>
        </input>
        <output>
            <collision-output value="''' + collision_output + '''"/>
        </output>
        <time>
            <begin value="''' + start_sec + '''"/>
            <end value="''' + time_sec + '''"/>
        </time>
        <processing>
            <collision.action value="''' + coll_action + '''"/>
            <collision.mingap-factor value="''' + coll_mingap_factor + '''"/>
            <collision.stoptime value="'''+ coll_stoptime + '''"/>
            <collision.check-junctions value="''' + coll_check_junctions + '''"/>
            <collision.check-junctions.mingap value="''' + coll_check_junctions_mingap + '''"/>
        </processing>
        <ssm_device>
            <device.ssm.probability value="0"/>
            <device.ssm.file value="''' + ssm_file + '''"/>
        </ssm_device>
        <time-to-teleport value="-1"/>
    </configuration> 
    '''

    config2 = '''<?xml version="1.0" encoding="iso-8859-1"?>
    <configuration xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance"
    xsi:noNamespaceSchemaLocation="http://sumo.dlr.de/xsd/sumoConfiguration.xsd">
        <input>
            <net-file value="''' + netwo_file_name + '''"/>
            <route-files value="''' + route_file_name + '''"/>
        </input>
        <time>
            <begin value="0"/>
            <end value="''' + time_sec + '''"/>
        </time>
        <time-to-teleport value="-1"/>
    </configuration> 
    '''

    f = open(confi_file_name, "w")
    f.write(config)
    f.close()

<lanechange-output value="''' + lane_change_output + '''"/>
            <processing>
                <collision.action" type="strOptionType" minOccurs="0"/>
                <collision.stoptime" type="timeOptionType" minOccurs="0"/>
                <collision.check-junctions" type="boolOptionType" minOccurs="0"/>
                <collision.check-junctions.mingap" type="floatOptionType" minOccurs="0"/>
                <collision.mingap-factor" type="floatOptionType" minOccurs="0"/>
            </processing>

                <device.ssm.explicit" type="strArrayOptionType" minOccurs="0"/>
                <device.ssm.deterministic" type="boolOptionType" minOccurs="0"/>

                <device.ssm.measures" type="strOptionType" minOccurs="0"/>
                <device.ssm.thresholds" type="strOptionType" minOccurs="0"/>
                <device.ssm.trajectories" type="boolOptionType" minOccurs="0"/>
                <device.ssm.range" type="floatOptionType" minOccurs="0"/>
                <device.ssm.extratime" type="floatOptionType" minOccurs="0"/>
                <device.ssm.file" type="strOptionType" minOccurs="0"/>
                <device.ssm.geo" type="boolOptionType" minOccurs="0"/>
                <device.ssm.write-positions" type="boolOptionType" minOccurs="0"/>
                <device.ssm.write-lane-positions" type="boolOptionType" minOccurs="0"/>

In [ ]:
write_config_file(0, 3600, 1)

### 3.3. RUN SIM

In [ ]:
!sumo flowrouter.sumocfg

Step #3600.00 (106ms ~= 9.43*RT, ~38150.94UPS, vehicles TOT 26398 ACT 4044 BUF 12782)     


In [ ]:
POUBELLE

In [ ]:
def convertion_in_lon_lat(pems_path, lat_log_file, file_inductor):
    
    lat_log_path = pems_path + "/" + lat_log_file
    path_inductor = pems_path + "/" + file_inductor

    df_lat_log = pd.read_excel(lat_log_path)
    df_inductor = pd.read_excel(path_inductor)

    #Convertion
    list_lat = []
    list_log = []
    for row in range(df_inductor.shape[0]):
        #FIND INDEX OF CLOSEST VALUE
        list_pm = df_lat_log['Abs PM'].tolist()
        indx = min(range(len(list_pm)), key=lambda i: abs(list_pm[i]-df_inductor['Abs PM'][row]))

        list_lat.append(df_lat_log.Latitude[indx])
        list_log.append(df_lat_log.Longitude[indx])

    #Add new columns
    df_inductor["lat"] = list_lat
    df_inductor["lon"] = list_log

    #Clean the file and save as an array
    df_inductor = df_inductor[["VDS", "lat", "lon"]]
    df_inductor_array = df_inductor.to_numpy()

    return df_inductor_array